In [1]:
# Import all the necessary modules
import os
import sys
import os, sys
# from .../research/notebooks -> go up two levels to repo root
repo_root = os.path.abspath(os.path.join(os.getcwd(), "..", ".."))
if repo_root not in sys.path:
    sys.path.insert(0, repo_root)

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import matplotlib.ticker as mtick
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn import linear_model
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score 
import pandas_datareader as pdr
import math
import datetime as dt
from datetime import datetime, timezone
import itertools
import ast
import yfinance as yf
import seaborn as sn
import yaml
import requests
from pathlib import Path
from IPython.display import display, HTML
from strategy_signal.trend_following_signal import (
    apply_jupyter_fullscreen_css, get_trend_donchian_signal_for_portfolio_with_rolling_r_sqr_vol_of_vol
)
from portfolio.strategy_performance import (calculate_sharpe_ratio, calculate_calmar_ratio, calculate_CAGR, calculate_risk_and_performance_metrics,
                                          calculate_compounded_cumulative_returns, estimate_fee_per_trade, rolling_sharpe_ratio)
from utils import coinbase_utils as cn
from portfolio import strategy_performance as perf
from sizing import position_sizing_binary_utils as size_bin
from sizing import position_sizing_continuous_utils as size_cont
from strategy_signal import trend_following_signal as tf
%matplotlib inline

In [2]:
import importlib
importlib.reload(cn)
importlib.reload(perf)
importlib.reload(tf)
importlib.reload(size_bin)
importlib.reload(size_cont)

<module 'sizing.position_sizing_continuous_utils' from '/Users/adheerchauhan/Documents/git/trend_following/sizing/position_sizing_continuous_utils.py'>

In [3]:
import warnings
warnings.filterwarnings('ignore')
pd.set_option('Display.max_rows', None)
pd.set_option('Display.max_columns',None)
apply_jupyter_fullscreen_css()

## Coinbase Utility Functions

In [5]:
def get_coinbase_historical_price_data(
    client,
    ticker,
    start_timestamp,
    end_timestamp,
    granularity="ONE_DAY",
    retries=3,
    delay=5,
):
    """
    Generic candle puller for Coinbase Advanced Trade RESTClient.get_candles().

    granularity examples:
      ONE_MINUTE, FIVE_MINUTE, FIFTEEN_MINUTE, THIRTY_MINUTE,
      ONE_HOUR, TWO_HOUR, FOUR_HOUR, SIX_HOUR, ONE_DAY
    """
    attempts = 0
    while attempts < retries:
        try:
            candle_list = client.get_candles(
                product_id=ticker,
                start=int(start_timestamp),
                end=int(end_timestamp),
                granularity=granularity,
            ).candles

            if not candle_list:
                cols = ["open", "high", "low", "close", "volume"]
                return pd.DataFrame(columns=cols).rename_axis("date")

            candle_data = []
            for c in candle_list:
                candle_data.append(
                    {
                        "date": c["start"],  # epoch seconds
                        "low": float(c["low"]),
                        "high": float(c["high"]),
                        "open": float(c["open"]),
                        "close": float(c["close"]),
                        "volume": float(c["volume"]),
                    }
                )

            df = pd.DataFrame(candle_data)
            if df.empty or "date" not in df.columns:
                cols = ["open", "high", "low", "close", "volume"]
                return pd.DataFrame(columns=cols).rename_axis("date")

            # epoch seconds -> tz-aware UTC -> drop tz (tz-naive UTC)
            s = pd.to_datetime(pd.to_numeric(df["date"], errors="coerce"), unit="s", utc=True).dt.tz_localize(None)

            # Only normalize for daily bars; keep intraday timestamps intact
            if granularity == "ONE_DAY":
                s = s.dt.normalize()

            df["date"] = s
            df = df.set_index("date").sort_index().rename_axis("date")

            return df

        except requests.exceptions.ConnectionError as e:
            print(f"Connection error: {e}. Retrying in {delay} seconds...")
            attempts += 1
            time.sleep(delay)

    raise Exception("Max retries exceeded. Could not connect to Coinbase API.")


In [6]:
def save_historical_crypto_prices_from_coinbase(
    ticker,
    user_start_date=False,
    start_date=None,
    end_date=None,
    save_to_file=False,
    portfolio_name="Default",
    granularity="ONE_DAY",
):
    """
    Pull historical candles for a single ticker at the requested granularity.

    Note: Coinbase candle endpoints have request caps (commonly 300 candles per call),
    so we chunk requests.
    """
    client = cn.get_coinbase_rest_api_client(portfolio_name=portfolio_name)

    if user_start_date:
        start_date = pd.Timestamp(start_date)
    else:
        start_date = cn.coinbase_start_date_by_ticker_dict.get(ticker)
        start_date = pd.Timestamp(start_date)
        if start_date is None:
            print(f"Start date for {ticker} is not included in the dictionary!")
            return None

    end_date = pd.Timestamp(end_date)

    # seconds per bar (used to step chunks without gaps)
    granularity_to_seconds = {
        "ONE_MINUTE": 60,
        "FIVE_MINUTE": 300,
        "FIFTEEN_MINUTE": 900,
        "THIRTY_MINUTE": 1800,
        "ONE_HOUR": 3600,
        "TWO_HOUR": 7200,
        "FOUR_HOUR": 14400,
        "SIX_HOUR": 21600,
        "ONE_DAY": 86400,
    }
    bar_sec = granularity_to_seconds.get(granularity)
    if bar_sec is None:
        raise ValueError(f"Unsupported granularity: {granularity}")

    # Keep your old 6-week chunking (works great for ONE_DAY and FOUR_HOUR),
    # but ensure we never step by +1 day when doing intraday.
    temp_start = start_date
    current_end = temp_start

    dfs = []
    while current_end < end_date:
        # 6 weeks is safe for FOUR_HOUR (≈252 candles) under the typical 300 limit :contentReference[oaicite:1]{index=1}
        current_end = pd.to_datetime(temp_start) + dt.timedelta(weeks=6)
        if current_end > end_date:
            current_end = end_date

        start_ts = int(pd.Timestamp(temp_start).timestamp())
        end_ts = int(pd.Timestamp(current_end).timestamp())

        df_chunk = get_coinbase_historical_price_data(
            client=client,
            ticker=ticker,
            start_timestamp=start_ts,
            end_timestamp=end_ts,
            granularity=granularity,
        )
        dfs.append(df_chunk)

        # advance by exactly one bar to avoid duplicates and avoid gaps
        temp_start = pd.to_datetime(current_end) + pd.Timedelta(seconds=bar_sec)

    if not dfs:
        cols = ["open", "high", "low", "close", "volume"]
        return pd.DataFrame(columns=cols).rename_axis("date")

    df = pd.concat(dfs, axis=0)
    df = df[~df.index.duplicated(keep="last")].sort_index()

    # optional: save_to_file logic can stay as you had it (not shown in your snippet)

    return df


In [12]:
cn_ticker_list = cn.coinbase_start_date_by_ticker_dict

In [14]:
cn_ticker_list

{'BTC-USD': '2016-01-01',
 'ETH-USD': '2016-06-01',
 'SOL-USD': '2021-06-01',
 'ADA-USD': '2021-03-01',
 'AVAX-USD': '2021-09-01',
 'DOT-USD': '2021-06-01',
 'ATOM-USD': '2020-01-01',
 'LTC-USD': '2016-09-01',
 'XRP-USD': '2023-06-01',
 'ALGO-USD': '2019-08-01',
 'XLM-USD': '2019-02-01',
 'TON-USD': '2025-11-18',
 'NEAR-USD': '2022-09-01',
 'ICP-USD': '2021-05-10',
 'HBAR-USD': '2022-10-13',
 'SUI-USD': '2023-05-18',
 'CRO-USD': '2021-11-01',
 'APT-USD': '2022-10-19',
 'XTZ-USD': '2019-08-06',
 'EGLD-USD': '2022-12-07',
 'FIL-USD': '2020-12-09',
 'SEI-USD': '2023-08-15',
 'TIA-USD': '2023-11-01',
 'KAVA-USD': '2023-01-19',
 'ROSE-USD': '2022-04-26',
 'MATIC-USD': '2021-02-01',
 'SKL-USD': '2021-02-01',
 'OP-USD': '2022-06-01',
 'ARB-USD': '2023-03-23',
 'POL-USD': '2024-09-04',
 'IMX-USD': '2021-12-09',
 'STRK-USD': '2024-02-21',
 'BLAST-USD': '2024-06-26',
 'ZK-USD': '2024-09-25',
 'LRC-USD': '2020-09-15',
 'ZORA-USD': '2025-04-24',
 'METIS-USD': '2022-06-28',
 'STX-USD': '2022-01-20'

In [16]:
ticker_list = []
exclude_list = ['USDT-USD','DAI-USD','USD1-USD','PAX-USD','MATIC-USD']
for ticker, date in cn_ticker_list.items():
    if (pd.Timestamp(cn_ticker_list[ticker]).date() <= pd.Timestamp('2022-04-01').date()) & (ticker not in exclude_list):
        ticker_list.append(ticker)

In [18]:
print(len(ticker_list))
ticker_list

40


['BTC-USD',
 'ETH-USD',
 'SOL-USD',
 'ADA-USD',
 'AVAX-USD',
 'DOT-USD',
 'ATOM-USD',
 'LTC-USD',
 'ALGO-USD',
 'XLM-USD',
 'ICP-USD',
 'CRO-USD',
 'XTZ-USD',
 'FIL-USD',
 'SKL-USD',
 'IMX-USD',
 'LRC-USD',
 'STX-USD',
 'DOGE-USD',
 'SHIB-USD',
 'LINK-USD',
 'FET-USD',
 'GRT-USD',
 'RNDR-USD',
 'OXT-USD',
 'AIOZ-USD',
 'DIA-USD',
 'KRL-USD',
 'UNI-USD',
 'AAVE-USD',
 'AMP-USD',
 'COMP-USD',
 'MKR-USD',
 'SNX-USD',
 'SUSHI-USD',
 'CRV-USD',
 'BAL-USD',
 '1INCH-USD',
 'MANA-USD',
 'REQ-USD']

In [20]:
%%time
start_date = "2022-04-01"
end_date   = "2024-12-31"

df_list = []
df_by_ticker = {}
ticker_list_len = len(ticker_list)
loop_start = 0
loop_end = 0
counter = 0
while counter < ticker_list_len:
    loop_start = counter
    if counter == 40:
        loop_end = ticker_list_len
    else:
        loop_end = counter + 10
    print(counter, loop_start, loop_end, ticker_list[loop_start: loop_end])
    for t in ticker_list[loop_start: loop_end]:
        df_by_ticker[t] = save_historical_crypto_prices_from_coinbase(
            ticker=t,
            user_start_date=True,
            start_date=start_date,
            end_date=end_date,
            portfolio_name="Default",
            granularity="FOUR_HOUR",
        )
    counter += 10

    # Optional: one combined frame (MultiIndex: ticker, date)
    df_all = pd.concat(df_by_ticker, names=["ticker", "date"]).sort_index()
    df_list.append(df_all)

0 0 10 ['BTC-USD', 'ETH-USD', 'SOL-USD', 'ADA-USD', 'AVAX-USD', 'DOT-USD', 'ATOM-USD', 'LTC-USD', 'ALGO-USD', 'XLM-USD']
10 10 20 ['ICP-USD', 'CRO-USD', 'XTZ-USD', 'FIL-USD', 'SKL-USD', 'IMX-USD', 'LRC-USD', 'STX-USD', 'DOGE-USD', 'SHIB-USD']
20 20 30 ['LINK-USD', 'FET-USD', 'GRT-USD', 'RNDR-USD', 'OXT-USD', 'AIOZ-USD', 'DIA-USD', 'KRL-USD', 'UNI-USD', 'AAVE-USD']
30 30 40 ['AMP-USD', 'COMP-USD', 'MKR-USD', 'SNX-USD', 'SUSHI-USD', 'CRV-USD', 'BAL-USD', '1INCH-USD', 'MANA-USD', 'REQ-USD']
CPU times: user 13.2 s, sys: 1.51 s, total: 14.7 s
Wall time: 1min 58s


In [178]:
len(df_list)

4

In [22]:
df_all.shape

(241229, 5)

In [26]:
len(df_all.index.unique())

241229

In [194]:
ticker_cond = (df_all.index.get_level_values('ticker') == 'ADA-USD')
df_all[ticker_cond].tail(200)

low    high    open   close        volume
ticker  date                                                             
ADA-USD 2024-11-27 20:00:00  1.0012  1.0399  1.0194  1.0123  1.410101e+07
        2024-11-28 00:00:00  0.9889  1.0316  1.0132  1.0071  1.156654e+07
        2024-11-28 04:00:00  0.9909  1.0268  1.0068  0.9968  5.799917e+06
        2024-11-28 08:00:00  0.9818  1.0037  0.9970  0.9976  6.108932e+06
        2024-11-28 12:00:00  0.9705  1.0103  0.9972  0.9775  9.179363e+06
        2024-11-28 16:00:00  0.9774  1.0072  0.9776  1.0021  6.670803e+06
        2024-11-28 20:00:00  0.9955  1.0492  1.0022  1.0323  1.161228e+07
        2024-11-29 00:00:00  1.0278  1.0620  1.0321  1.0489  1.497607e+07
        2024-11-29 04:00:00  1.0357  1.0790  1.0491  1.0458  1.290120e+07
        2024-11-29 08:00:00  1.0435  1.0875  1.0457  1.0651  1.078638e+07
        2024-11-29 12:00:00  1.0542  1.1000  1.0645  1.0761  1.839468e+07
        2024-11-29 16:00:00  1.0390  1.0837  1.0762  1.0521  1.785688e+07
        2024-11-29 20:00:00  1.0450  1.0861  1.0521  1.0761  1.403409e+07
        2024-11-30 00:00:00  1.0505  1.0885  1.0755  1.0697  1.469869e+07
        2024-11-30 04:00:00  1.0604  1.1450  1.0699  1.1299  2.163621e+07
        2024-11-30 08:00:00  1.0778  1.1500  1.1298  1.0956  1.549969e+07
        2024-11-30 12:00:00  1.0716  1.0965  1.0956  1.0929  9.953565e+06
        2024-11-30 16:00:00  1.0800  1.0959  1.0929  1.0866  7.705551e+06
        2024-11-30 20:00:00  1.0736  1.0978  1.0862  1.0797  1.199009e+07
        2024-12-01 00:00:00  1.0373  1.0857  1.0796  1.0511  1.483185e+07
        2024-12-01 04:00:00  1.0442  1.0610  1.0515  1.0572  5.513697e+06
        2024-12-01 08:00:00  1.0556  1.0788  1.0566  1.0722  5.476993e+06
        2024-12-01 12:00:00  1.0585  1.0755  1.0721  1.0742  7.516496e+06
        2024-12-01 16:00:00  1.0565  1.0984  1.0740  1.0946  1.689854e+07
        2024-12-01 20:00:00  1.0755  1.1647  1.0947  1.1503  4.851472e+07
        2024-12-02 00:00:00  1.1264  1.1913  1.1505  1.1403  4.316623e+07
        2024-12-02 04:00:00  1.1167  1.1689  1.1402  1.1416  2.022920e+07
        2024-12-02 08:00:00  1.0568  1.1585  1.1412  1.0731  2.124469e+07
        2024-12-02 12:00:00  1.0675  1.2261  1.0725  1.2078  4.767056e+07
        2024-12-02 16:00:00  1.1558  1.2428  1.2064  1.2192  5.063293e+07
        2024-12-02 20:00:00  1.1753  1.2339  1.2186  1.2024  2.134085e+07
        2024-12-03 00:00:00  1.1841  1.3278  1.2028  1.2982  5.896306e+07
        2024-12-03 04:00:00  1.2517  1.3126  1.2983  1.2682  3.060346e+07
        2024-12-03 08:00:00  1.2310  1.3140  1.2691  1.2858  1.837665e+07
        2024-12-03 12:00:00  1.1402  1.3199  1.2858  1.1978  4.949697e+07
        2024-12-03 16:00:00  1.1686  1.2264  1.1977  1.1897  2.512853e+07
        2024-12-03 20:00:00  1.1837  1.2365  1.1895  1.1920  2.169567e+07
        2024-12-04 00:00:00  1.1809  1.2199  1.1930  1.2096  1.624852e+07
        2024-12-04 04:00:00  1.2091  1.2414  1.2095  1.2299  1.086193e+07
        2024-12-04 08:00:00  1.2173  1.2420  1.2298  1.2243  8.387761e+06
        2024-12-04 12:00:00  1.1852  1.2287  1.2242  1.1914  1.832581e+07
        2024-12-04 16:00:00  1.1407  1.1980  1.1915  1.1923  3.300019e+07
        2024-12-04 20:00:00  1.1649  1.2120  1.1923  1.1887  2.184292e+07
        2024-12-05 00:00:00  1.1163  1.2400  1.1886  1.1829  4.667123e+07
        2024-12-05 04:00:00  1.1735  1.2140  1.1830  1.2068  1.560264e+07
        2024-12-05 08:00:00  1.2055  1.2384  1.2069  1.2249  1.388446e+07
        2024-12-05 12:00:00  1.1857  1.2343  1.2248  1.2118  1.977112e+07
        2024-12-05 16:00:00  1.1861  1.2461  1.2121  1.1889  2.221459e+07
        2024-12-05 20:00:00  1.1435  1.2085  1.1891  1.1612  2.372577e+07
        2024-12-06 00:00:00  1.1530  1.1947  1.1614  1.1887  1.418680e+07
        2024-12-06 04:00:00  1.1849  1.2012  1.1887  1.1895  7.217247e+06
        2024-12-06 08:00:00  1.1502  1.1941  1.1893  1.1628  9.525318e+06
        2024-12-06 12:00:00  1.1358 

In [28]:
df_all.reset_index().groupby(['ticker']).size()

ticker
1INCH-USD    6031
AAVE-USD     6031
ADA-USD      6031
AIOZ-USD     6031
ALGO-USD     6031
AMP-USD      6031
ATOM-USD     6031
AVAX-USD     6031
BAL-USD      6031
BTC-USD      6031
COMP-USD     6031
CRO-USD      6031
CRV-USD      6031
DIA-USD      6031
DOGE-USD     6031
DOT-USD      6031
ETH-USD      6031
FET-USD      6031
FIL-USD      6031
GRT-USD      6031
ICP-USD      6031
IMX-USD      6031
KRL-USD      6020
LINK-USD     6031
LRC-USD      6031
LTC-USD      6031
MANA-USD     6031
MKR-USD      6031
OXT-USD      6031
REQ-USD      6031
RNDR-USD     6031
SHIB-USD     6031
SKL-USD      6031
SNX-USD      6031
SOL-USD      6031
STX-USD      6031
SUSHI-USD    6031
UNI-USD      6031
XLM-USD      6031
XTZ-USD      6031
dtype: int64

## Build Return Features

In [83]:
df_returns = df_all.copy()
df_returns = df_returns.reset_index()

In [85]:
df_returns = df_returns.sort_values(["ticker", "date"])
df_returns["close_t_4h"] = df_returns.groupby("ticker")["close"].shift(1)
df_returns["ret_4h"] = np.log(df_returns["close"] / df_returns["close_t_4h"])

In [125]:
df = df_returns.copy()
df = df.sort_values(["date", "ticker"])  # important for reproducibility

# optional: drop insane outliers or bad data points
df = df[np.isfinite(df["ret_4h"])].reset_index(drop=True)

# cross-sectional mean/std at each bar
cs_mean = df.groupby("date")["ret_4h"].transform("mean")
cs_std  = df.groupby("date")["ret_4h"].transform("std").replace(0, np.nan)

df["z_ret_4h"] = (df["ret_4h"] - cs_mean) / cs_std

In [127]:
df.shape

(241189, 10)

In [129]:
min_names = 20  # for example
n_names = df.groupby("date")["ticker"].transform("nunique")
df = df[n_names >= min_names]

In [133]:
df.shape

(241189, 10)

In [135]:
H = 3  # 12h ahead
g_open = df.groupby("ticker")["open"]
df["fwd_ret_open_H"] = np.log(g_open.shift(-(H+1)) / g_open.shift(-1))

In [147]:
g_open.shift(-(H+1))

0              1.881000
1            259.950000
2              1.173300
3              0.242600
4              0.941800
5              0.027360
6             29.610000
7             99.120000
8             16.210000
9          46390.410000
10           157.750000
11             0.480400
12             2.810000
13             1.090000
14             0.141400
15            22.020000
16          3471.400000
17             0.482500
18            24.780000
19             0.494300
20            21.630000
21             2.483000
22             0.958300
23            17.230000
24             1.212600
25           126.290000
26             2.678000
27          2343.920000
28             0.296500
29             0.264800
30             3.050000
31             0.000026
32             0.286200
33             7.812000
34           137.460000
35             1.460000
36             4.670000
37            11.910000
38             0.231710
39             3.950000
40             1.879000
41           244

In [137]:
df.head(20)

ticker                date          low        high         open  \
0   1INCH-USD 2022-04-01 04:00:00      1.70700      1.7560      1.70900   
1    AAVE-USD 2022-04-01 04:00:00    215.02000    230.6400    217.89000   
2     ADA-USD 2022-04-01 04:00:00      1.11910      1.1512      1.12370   
3    AIOZ-USD 2022-04-01 04:00:00      0.23170      0.2360      0.23390   
4    ALGO-USD 2022-04-01 04:00:00      0.90310      0.9380      0.90420   
5     AMP-USD 2022-04-01 04:00:00      0.02645      0.0270      0.02645   
6    ATOM-USD 2022-04-01 04:00:00     27.91000     28.6800     28.08000   
7    AVAX-USD 2022-04-01 04:00:00     91.57000     94.4000     92.30000   
8     BAL-USD 2022-04-01 04:00:00     15.47000     15.8900     15.60000   
9     BTC-USD 2022-04-01 04:00:00  44554.06000  45115.7000  44612.73000   
10   COMP-USD 2022-04-01 04:00:00    143.66000    150.1600    143.74000   
11    CRO-USD 2022-04-01 04:00:00      0.44910      0.4605      0.45030   
12    CRV-USD 2022-04-01 04:00:00      2.61600      2.6860      2.62000   
13    DIA-USD 2022-04-01 04:00:00      1.05000      1.0800      1.07000   
14   DOGE-USD 2022-04-01 04:00:00      0.13420      0.1367      0.13490   
15    DOT-USD 2022-04-01 04:00:00     20.90000     21.4100     20.94000   
16    ETH-USD 2022-04-01 04:00:00   3243.63000   3283.0000   3251.01000   
17    FET-USD 2022-04-01 04:00:00      0.43070      0.4650      0.43290   
18    FIL-USD 2022-04-01 04:00:00     23.13000     23.7900     23.35000   
19    GRT-USD 2022-04-01 04:00:00      0.44300      0.4632      0.44500   

          close        volume   close_t_4h    ret_4h  z_ret_4h  fwd_ret_open_H  
0       1.75500  6.485885e+04      1.70800  0.027146  0.152888        0.068196  
1     225.85000  3.136698e+04    217.93000  0.035697  0.466146        0.140353  
2       1.15120  9.031584e+06      1.12420  0.023733  0.027878        0.018929  
3       0.23400  1.090815e+05      0.23530 -0.005540 -1.044476        0.039946  
4       0.93510  2.297936e+06      0.90430  0.033492  0.385377        0.007139  
5       0.02675  2.874114e+07      0.02651  0.009012 -0.511378        0.023296  
6      28.67000  9.591230e+04     28.07000  0.021150 -0.066755        0.032261  
7      94.25000  1.297425e+05     92.30000  0.020907 -0.075664        0.050380  
8      15.81000  1.589222e+04     15.61000  0.012731 -0.375162        0.023721  
9   45030.70000  1.866921e+03  44614.99000  0.009275 -0.501776        0.029748  
10    150.01000  4.522923e+03    143.77000  0.042487  0.714880        0.049976  
11      0.46030  2.962519e+06      0.45020  0.022187 -0.028781        0.042306  
12      2.68300  4.387325e+05      2.62400  0.022236 -0.026979        0.045876  
13      1.06000  2.287560e+04      1.07000 -0.009390 -1.185494        0.027909  
14      0.13650  2.596924e+07      0.13490  0.011791 -0.409599        0.035268  
15     21.40000  8.624681e+04     20.93000  0.022207 -0.028016        0.028560  
16   3279.89000  1.577987e+04   3250.89000  0.008881 -0.516191        0.056711  
17      0.46470  8.106551e+05      0.43200  0.072966  1.831409        0.038235  
18     23.76000  1.449417e+05     23.35000  0.017407 -0.203884        0.042033  
19      0.46120  5.755184e+06      0.44470  0.036432  0.493061        0.069311

In [121]:
df[df.date == pd.Timestamp('2022-04-01 04:00:00')].sort_values('z_ret_4h')#.head()#.loc[6000:6050]#.head()#.groupby([ticker])['close']#.shift(1)

ticker                date           low          high          open  \
13    DIA-USD 2022-04-01 04:00:00      1.050000      1.080000      1.070000   
22    KRL-USD 2022-04-01 04:00:00      0.909300      0.929600      0.926000   
33    SNX-USD 2022-04-01 04:00:00      6.741000      7.213000      7.037000   
3    AIOZ-USD 2022-04-01 04:00:00      0.231700      0.236000      0.233900   
29    REQ-USD 2022-04-01 04:00:00      0.243600      0.248100      0.246700   
27    MKR-USD 2022-04-01 04:00:00   2031.190000   2074.810000   2064.410000   
16    ETH-USD 2022-04-01 04:00:00   3243.630000   3283.000000   3251.010000   
5     AMP-USD 2022-04-01 04:00:00      0.026450      0.027000      0.026450   
38    XLM-USD 2022-04-01 04:00:00      0.222667      0.226189      0.223869   
9     BTC-USD 2022-04-01 04:00:00  44554.060000  45115.700000  44612.730000   
14   DOGE-USD 2022-04-01 04:00:00      0.134200      0.136700      0.134900   
31   SHIB-USD 2022-04-01 04:00:00      0.000025      0.000026      0.000025   
8     BAL-USD 2022-04-01 04:00:00     15.470000     15.890000     15.600000   
37    UNI-USD 2022-04-01 04:00:00     11.050000     11.280000     11.120000   
25    LTC-USD 2022-04-01 04:00:00    120.830000    122.850000    120.980000   
30   RNDR-USD 2022-04-01 04:00:00      2.840000      2.890000      2.860000   
35    STX-USD 2022-04-01 04:00:00      1.390000      1.430000      1.400000   
20    ICP-USD 2022-04-01 04:00:00     20.190000     20.860000     20.500000   
18    FIL-USD 2022-04-01 04:00:00     23.130000     23.790000     23.350000   
7    AVAX-USD 2022-04-01 04:00:00     91.570000     94.400000     92.300000   
6    ATOM-USD 2022-04-01 04:00:00     27.910000     28.680000     28.080000   
11    CRO-USD 2022-04-01 04:00:00      0.449100      0.460500      0.450300   
15    DOT-USD 2022-04-01 04:00:00     20.900000     21.410000     20.940000   
12    CRV-USD 2022-04-01 04:00:00      2.616000      2.686000      2.620000   
26   MANA-USD 2022-04-01 04:00:00      2.518000      2.586000      2.526000   
23   LINK-USD 2022-04-01 04:00:00     16.430000     16.850000     16.450000   
2     ADA-USD 2022-04-01 04:00:00      1.119100      1.151200      1.123700   
28    OXT-USD 2022-04-01 04:00:00      0.268300      0.279600      0.269600   
21    IMX-USD 2022-04-01 04:00:00      2.275000      2.365000      2.298000   
0   1INCH-USD 2022-04-01 04:00:00      1.707000      1.756000      1.709000   
39    XTZ-USD 2022-04-01 04:00:00      3.600000      3.710000      3.600000   
36  SUSHI-USD 2022-04-01 04:00:00      4.250000      4.410000      4.250000   
4    ALGO-USD 2022-04-01 04:00:00      0.903100      0.938000      0.904200   
1    AAVE-USD 2022-04-01 04:00:00    215.020000    230.640000    217.890000   
34    SOL-USD 2022-04-01 04:00:00    120.000000    126.490000    122.010000   
19    GRT-USD 2022-04-01 04:00:00      0.443000      0.463200      0.445000   
10   COMP-USD 2022-04-01 04:00:00    143.660000    150.160000    143.740000   
24    LRC-USD 2022-04-01 04:00:00      1.120500      1.174200      1.122100   
17    FET-USD 2022-04-01 04:00:00      0.430700      0.465000      0.432900   
32    SKL-USD 2022-04-01 04:00:00      0.242400      0.292100      0.242500   

           close        volume    close_t_4h    ret_4h  z_ret_4h  
13      1.060000  2.287560e+04      1.070000 -0.009390 -1.185494  
22      0.918100  2.332620e+04      0.926000 -0.008568 -1.155389  
33      7.001000  3.392724e+05      7.045000 -0.006265 -1.071033  
3       0.234000  1.090815e+05      0.235300 -0.005540 -1.044476  
29      0.248000  2.753920e+05      0.246700  0.005256 -0.648996  
27   2074.810000  1.539963e+02   2060.910000  0.006722 -0.595285  
16   3279.890000  1.577987e+04   3250.890000  0.008881 -0.516191  
5       0.026750  2.874114e+07      0.026510  0.009012 -0.511378  
38      0.225855  1.012126e+07      0.223810  0.009096 -0.508328  
9   45030.700000  1.866921e+03  44614.990000  0.009275 -0.501776  
14      0.136500  2.596924e+07

In [141]:
df[df.ticker == 'AAVE-USD'].head(20)

ticker                date     low    high    open   close     volume  \
1    AAVE-USD 2022-04-01 04:00:00  215.02  230.64  217.89  225.85  31366.979   
41   AAVE-USD 2022-04-01 08:00:00  218.70  226.02  225.91  220.44  17916.536   
81   AAVE-USD 2022-04-01 12:00:00  214.00  248.95  220.44  245.02  68939.822   
121  AAVE-USD 2022-04-01 16:00:00  244.05  261.29  244.96  260.06  58259.449   
161  AAVE-USD 2022-04-01 20:00:00  243.50  260.64  259.95  244.76  23188.976   
201  AAVE-USD 2022-04-02 00:00:00  241.29  257.38  244.72  245.16  24991.545   
241  AAVE-USD 2022-04-02 04:00:00  240.98  246.28  245.33  243.16  10017.931   
281  AAVE-USD 2022-04-02 08:00:00  240.93  249.10  243.14  245.29  15393.770   
321  AAVE-USD 2022-04-02 12:00:00  235.80  247.67  245.22  238.06  20298.957   
361  AAVE-USD 2022-04-02 16:00:00  235.80  245.13  238.07  242.12  21907.784   
401  AAVE-USD 2022-04-02 20:00:00  235.80  247.26  242.16  238.39  19009.959   
441  AAVE-USD 2022-04-03 00:00:00  231.36  240.38  238.18  237.82  19419.940   
481  AAVE-USD 2022-04-03 04:00:00  237.39  248.04  237.97  242.35  24342.209   
521  AAVE-USD 2022-04-03 08:00:00  240.21  252.60  242.51  252.56  20506.806   
561  AAVE-USD 2022-04-03 12:00:00  241.61  252.78  252.57  242.22  28734.517   
601  AAVE-USD 2022-04-03 16:00:00  239.18  246.21  242.24  242.67  21205.878   
641  AAVE-USD 2022-04-03 20:00:00  242.41  248.69  242.73  243.27  10927.840   
681  AAVE-USD 2022-04-04 00:00:00  236.77  243.35  243.30  239.19  13222.758   
721  AAVE-USD 2022-04-04 04:00:00  237.15  241.45  239.14  240.13   8801.180   
761  AAVE-USD 2022-04-04 08:00:00  233.82  241.59  240.21  236.70  11821.898   

     close_t_4h    ret_4h  z_ret_4h  fwd_ret_open_H  
1        217.93  0.035697  0.466146        0.140353  
41       225.85 -0.024246 -0.924200        0.104489  
81       220.44  0.105714  3.053627        0.001509  
121      245.02  0.059573  2.057740       -0.066852  
161      260.06 -0.060634 -2.683907        0.002041  
201      244.76  0.001633 -0.423295       -0.030039  
241      245.16 -0.008191 -1.061711       -0.004039  
281      243.16  0.008722  0.318570       -0.029129  
321      245.29 -0.029918 -0.874969       -0.000420  
361      238.06  0.016911  1.239994        0.001444  
401      242.12 -0.015525 -0.326184        0.058662  
441      238.39 -0.002394 -0.638264        0.017784  
481      237.82  0.018869  0.429476        0.000907  
521      242.35  0.041266  2.767313       -0.037393  
561      252.56 -0.041802 -2.842028       -0.012880  
601      242.22  0.001856  0.222584       -0.010436  
641      242.67  0.002469 -0.454340       -0.028093  
681      243.27 -0.016914 -0.072590       -0.046213  
721      239.19  0.003922 -0.343964       -0.015058  
761      240.13 -0.014387 -0.152452        0.006615

In [151]:
np.log(259.95/217.89)

0.1764989565435383

In [167]:
H = 3  # 12h ahead
g_open = df[df.ticker == 'AAVE-USD'].groupby("ticker")["open"]
# df["fwd_ret_open_H"] = np.log(g_open.shift(-(H+1)) / g_open.shift(-1))

In [181]:
g_open

In [187]:
df[df.ticker == 'AAVE-USD']['open'].shift(-(H+1))

1         259.95
41        244.72
81        245.33
121       243.14
161       245.22
201       238.07
241       242.16
281       238.18
321       237.97
361       242.51
401       252.57
441       242.24
481       242.73
521       243.30
561       239.14
601       240.21
641       236.56
681       228.34
721       236.62
761       238.13
801       236.88
841       234.58
881       232.95
921       227.29
961       226.22
1001      221.11
1041      212.13
1081      214.67
1121      209.84
1161      199.02
1201      197.88
1241      191.08
1281      199.65
1321      203.76
1361      204.25
1401      196.94
1441      200.99
1481      202.02
1521      199.62
1561      197.26
1601      192.31
1641      195.10
1681      189.51
1721      183.16
1761      182.32
1801      182.26
1841      179.46
1881      177.39
1921      182.60
1961      184.85
2001      183.78
2041      179.06
2081      179.13
2121      180.35
2161      186.94
2201      176.37
2241      173.16
2281      172.98
2321      163.

In [189]:
df[df.ticker == 'AAVE-USD']['open'].shift(-1)

1         225.91
41        220.44
81        244.96
121       259.95
161       244.72
201       245.33
241       243.14
281       245.22
321       238.07
361       242.16
401       238.18
441       237.97
481       242.51
521       252.57
561       242.24
601       242.73
641       243.30
681       239.14
721       240.21
761       236.56
801       228.34
841       236.62
881       238.13
921       236.88
961       234.58
1001      232.95
1041      227.29
1081      226.22
1121      221.11
1161      212.13
1201      214.67
1241      209.84
1281      199.02
1321      197.88
1361      191.08
1401      199.65
1441      203.76
1481      204.25
1521      196.94
1561      200.99
1601      202.02
1641      199.62
1681      197.26
1721      192.31
1761      195.10
1801      189.51
1841      183.16
1881      182.32
1921      182.26
1961      179.46
2001      177.39
2041      182.60
2081      184.85
2121      183.78
2161      179.06
2201      179.13
2241      180.35
2281      186.94
2321      176.

In [191]:
df[df.ticker == 'AAVE-USD'].head(20)

ticker                date     low    high    open   close     volume  \
1    AAVE-USD 2022-04-01 04:00:00  215.02  230.64  217.89  225.85  31366.979   
41   AAVE-USD 2022-04-01 08:00:00  218.70  226.02  225.91  220.44  17916.536   
81   AAVE-USD 2022-04-01 12:00:00  214.00  248.95  220.44  245.02  68939.822   
121  AAVE-USD 2022-04-01 16:00:00  244.05  261.29  244.96  260.06  58259.449   
161  AAVE-USD 2022-04-01 20:00:00  243.50  260.64  259.95  244.76  23188.976   
201  AAVE-USD 2022-04-02 00:00:00  241.29  257.38  244.72  245.16  24991.545   
241  AAVE-USD 2022-04-02 04:00:00  240.98  246.28  245.33  243.16  10017.931   
281  AAVE-USD 2022-04-02 08:00:00  240.93  249.10  243.14  245.29  15393.770   
321  AAVE-USD 2022-04-02 12:00:00  235.80  247.67  245.22  238.06  20298.957   
361  AAVE-USD 2022-04-02 16:00:00  235.80  245.13  238.07  242.12  21907.784   
401  AAVE-USD 2022-04-02 20:00:00  235.80  247.26  242.16  238.39  19009.959   
441  AAVE-USD 2022-04-03 00:00:00  231.36  240.38  238.18  237.82  19419.940   
481  AAVE-USD 2022-04-03 04:00:00  237.39  248.04  237.97  242.35  24342.209   
521  AAVE-USD 2022-04-03 08:00:00  240.21  252.60  242.51  252.56  20506.806   
561  AAVE-USD 2022-04-03 12:00:00  241.61  252.78  252.57  242.22  28734.517   
601  AAVE-USD 2022-04-03 16:00:00  239.18  246.21  242.24  242.67  21205.878   
641  AAVE-USD 2022-04-03 20:00:00  242.41  248.69  242.73  243.27  10927.840   
681  AAVE-USD 2022-04-04 00:00:00  236.77  243.35  243.30  239.19  13222.758   
721  AAVE-USD 2022-04-04 04:00:00  237.15  241.45  239.14  240.13   8801.180   
761  AAVE-USD 2022-04-04 08:00:00  233.82  241.59  240.21  236.70  11821.898   

     close_t_4h    ret_4h  z_ret_4h  fwd_ret_open_H  
1        217.93  0.035697  0.466146        0.140353  
41       225.85 -0.024246 -0.924200        0.104489  
81       220.44  0.105714  3.053627        0.001509  
121      245.02  0.059573  2.057740       -0.066852  
161      260.06 -0.060634 -2.683907        0.002041  
201      244.76  0.001633 -0.423295       -0.030039  
241      245.16 -0.008191 -1.061711       -0.004039  
281      243.16  0.008722  0.318570       -0.029129  
321      245.29 -0.029918 -0.874969       -0.000420  
361      238.06  0.016911  1.239994        0.001444  
401      242.12 -0.015525 -0.326184        0.058662  
441      238.39 -0.002394 -0.638264        0.017784  
481      237.82  0.018869  0.429476        0.000907  
521      242.35  0.041266  2.767313       -0.037393  
561      252.56 -0.041802 -2.842028       -0.012880  
601      242.22  0.001856  0.222584       -0.010436  
641      242.67  0.002469 -0.454340       -0.028093  
681      243.27 -0.016914 -0.072590       -0.046213  
721      239.19  0.003922 -0.343964       -0.015058  
761      240.13 -0.014387 -0.152452        0.006615

In [193]:
np.log(259.95/225.91)

0.14035261496059384